## CS201: HW3 - Turing Machines

<p>
<script language="JavaScript">
    document.write("Last modified: " + document.lastModified)
</script>

The homework file is (https://zoo.cs.yale.edu/classes/cs201/Fall_2021/materials/hws/hw3.rkt)

Unless the problem specifies otherwise:
- (a) You may solve the problem using any method and any Racket constructs 
(*except* mutators, that is, <code>set!</code> and its relatives.)
- (b) You may write auxiliary procedure(s) in addition to the one(s) specified in the problem.  
Please include a comment for each one specifying what it does and giving one or more examples of it.
- (c) Please make your code as clear and readable as possible.
<p>
The topics of this assignment are:
a simulator for Turing machines and writing Turing machine programs.

In [1]:
(require racket)
(require racket/base)

### Turing Machines

Turing machines were described in the lectures; see also the lecture
notes on the course web page.  Here is a top-level procedure to
simulate a Turing machine starting from a given configuration until
either it halts or it has executed n steps.  The procedure returns
the list of the successive configurations of the computation,
starting with the initial one.  The length of the list of
configurations is one more than the number of steps taken by the
machine.


In [2]:
(define (simulate mach config n) 
  (cond
    ((<= n 0) (list config))
    ((halted? mach config) (list config))
    (else
     (cons config
           (simulate 
            mach (next-config mach config) (- n 1))))))

<code>mach</code> is a representation of a Turing machine
<code>config</code> is a representation of a configuration of the machine
<code>n</code> is the maximum number of steps to simulate
<p>
The procedures <code>halted?</code> and <code>next-config</code> will be written by you in the
problems below; you will then have a complete Turing machine
simulator.
<p>
The test solutions at the bottom specify a number of steps, n, that
the simulation should run before stopping.  Your code may in fact
need more steps to solve the given problem.  The auto-grade program
will account for this, allowing roughly twice as many steps for your
code to run.  Still, there is a limit.  We have yet to solve the
halting problem.
<p>
<code>(simulate-lite tm config n)</code> is like <code>simulate</code>, but does not return
the intermediate states - just the final tape contents.  Thus, we
    can use <code>simulate-lite</code> in the public tests without revealing the
Turing machine instructions.


In [3]:
(define (simulate-lite tm config n) 
  (cond
    ((<= n 0) 'timeout)
    ((halted? tm config) (list (conf-ltape config)
                               (conf-symbol config)
                               (conf-rtape config)))
    (else
     (simulate-lite
      tm (next-config tm config) (- n 1)))))

### Turing machine representation.

A Turing machine is represented as a list of instructions, 
where each instruction is a 5-tuple, represented as a struct
defined as follows:

In [2]:
(struct ins (c-state c-symbol n-state n-symbol dir) #:transparent)

The fields represent the following components of an instruction:
current state, current symbol, new state, new symbol, and move direction

The current state and new state are Racket symbols, the current
symbol and new symbol are Racket symbols or non-negative integers
and the move direction must be either the symbol <code>'L</code> or the symbol
<code>'R</code>, representing a move to the left or right, respectively.
<p>

We discussed the <code>struct</code> special form in (https://zoo.cs.yale.edu/classes/cs201/Fall_2021/lectures/Structs.html)
    
Here is an example of an instruction struct.

In [3]:
(define i1 (ins 'q1 0 'q3 1 'L))

creates an instruction with current state <code>'q1</code>, current symbol <code>0</code>, new
state <code>'q3</code>, new symbol <code>1</code>, and move direction <code>'L</code>, and names it <code>i1</code>.

Because we've made <code>ins</code> "transparent", its field values
will be printed out.

In [4]:
i1

(ins 'q1 0 'q3 1 'L)

We can access the components of <code>i1</code> via the struct selectors:

In [5]:
(ins-c-state i1)

'q1

In [6]:
(ins-c-symbol i1)

0

In [7]:
(ins-n-state i1)

'q3

In [8]:
(ins-n-symbol i1)

1

In [9]:
(ins-dir i1)

'L

### Example (from lecture):

A Turing machine that when started in state <code>'q1</code> on the leftmost of a
string of 0's and 1's changes all the 0's to 1's and all the 1's to
0's and then returns the head to the leftmost symbol and halts.

In [10]:
(define tm1 
  (list
   (ins 'q1 0 'q1 1 'R)
   (ins 'q1 1 'q1 0 'R)
   (ins 'q1 'b 'q2 'b 'L)
   (ins 'q2 0 'q2 0 'L)
   (ins 'q2 1 'q2 1 'L)
   (ins 'q2 'b 'q3 'b 'R)))

### Another example (from lecture notes)

Below is the Turing machine from the <a target=wer href="https://zoo.cs.yale.edu/classes/cs201/topics/topic-TM.pdf">lecture notes</a>, which we simulated in class, with your classmates in the roles of the states of the machine.  This machine makes a copy of its input on the tape, separated by the symbol <tt>c</t>.  It is also available in the file: <a target=tt href="tmcopy.rkt">tmcopy.rkt</a>.

In [14]:
(define tmcopy
  (list                        
   (ins 'q1 0 'q1 0 'R)        
   (ins 'q1 1 'q1 1 'R)        
   (ins 'q1 'b 'q2 'c 'L)      
   (ins 'q2 0 'q2 0 'L)        
   (ins 'q2 1 'q2 1 'L)        
   (ins 'q2 'b 'q3 'b 'R)      
   (ins 'q3 0 'q4 'd 'R)       
   (ins 'q3 1 'q5 'e 'R)       
   (ins 'q3 'c 'q7 'c 'L) 
   (ins 'q4 0 'q4 0 'R) 
   (ins 'q4 1 'q4 1 'R) 
   (ins 'q4 'c 'q4 'c 'R) 
   (ins 'q4 'b 'q6 0 'L) 
   (ins 'q5 0 'q5 0 'R) 
   (ins 'q5 1 'q5 1 'R) 
   (ins 'q5 'c 'q5 'c 'R) 
   (ins 'q5 'b 'q6 1 'L) 
   (ins 'q6 0 'q6 0 'L) 
   (ins 'q6 1 'q6 1 'L) 
   (ins 'q6 'c 'q6 'c 'L) 
   (ins 'q6 'd 'q3 0 'R) 
   (ins 'q6 'e 'q3 1 'R) 
   (ins 'q7 0 'q7 0 'L) 
   (ins 'q7 1 'q7 1 'L) 
   (ins 'q7 'b 'q8 'b 'R)
   ))

Unfortunately, we cannot load the compiled solution into the jupyter notebook.

In [15]:
(enter! "hw3_rkt.zo")

enter!: undefined;
 cannot reference an identifier before its definition
  in module: top-level
  context...:
   eval-one-top12
   /usr/share/racket/pkgs/sandbox-lib/racket/sandbox.rkt:510:0: call-with-custodian-shutdown
   /usr/share/racket/collects/racket/private/more-scheme.rkt:148:2: call-with-break-parameterization
   .../more-scheme.rkt:261:28
   /usr/share/racket/pkgs/sandbox-lib/racket/sandbox.rkt:878:5: loop


So, execute the following code in racket when connected to a zoo machine:

<pre>
(enter! "hw3_rkt.zo")
tm1

(simulate tm1 (conf 'q1 '() 0 '(1 0 1 1 1)) 200)
(simulate-lite tm1 (conf 'q1 '() 0 '(1 0 1 1 1)) 200)
(simulate tm1 (conf 'q1 '() 0 '(0 0 0 0)) 200)

tmcopy

(simulate tmcopy (conf 'q1 '() 0 '(1 0 1 1 1)) 200)
(simulate-lite tmcopy (conf 'q1 '() 0 '(1 0 1 1 1)) 200)
(simulate tmcopy (conf 'q1 '() 1 '(0 0)) 200)  ;; example in notes

### problem 1 (15 points)

Define (in the format just given) a Turing machine named

<code>tm-reverse</code>

that takes an input string of 0's and 1's and produces an output
string equal to the reverse of the input string.  When the machine
halts, the head should be scanning the leftmost symbol of the
output.

That is, when started in state <code>q1</code> with the head on the leftmost of a
string of 0's and 1's, it halts with the head on the leftmost of a
string of 0's and 1's, and the output string is obtained from the
input string by reversing it.

Your machine *may* use additional tape symbols but the output should
contain no symbols other than 0, 1 and blank.  When the machine
halts, symbols other than the output should be blank.

Examples of the behavior of <code>tm-reverse</code>
<pre>
1            =>  1
110          =>  011
0001         =>  1000
101011       =>  110101

(test 'tm-reverse (simulate-lite tm-reverse (conf 'q1 '() 1 '()) 20) '(() 1 ()))
(test 'tm-reverse (simulate-lite tm-reverse (conf 'q1 '() 1 '(1 0)) 200) '(() 0 (1 1)))
(test 'tm-reverse (simulate-lite tm-reverse (conf 'q1 '() 0 '(0 0 1)) 200) '(() 1 (0 0 0)))
(test 'tm-reverse (simulate-lite tm-reverse (conf 'q1 '() 1 '(0 1 0 1 1)) 200) '(() 1 (1 0 1 0 1)))
</pre>

(It may help to review ideas from the machine <tt>tmcopy</tt> to make a copy of its input,
described in lectures and in the online lecture notes.)

The initial state of your machine should be <tt>q1</tt> -- other states may
be named with Racket symbols of your choice.

<b>IMPORTANT:</b> please describe how your Turing machine works.  You'll be
able to run it once you get the procedures for the simulator
working. Or you can load the working simulator from the staff solution: <code>hw3_rkt.zo</code>

In [20]:
(define tm-reverse
  empty)

empty: undefined;
 cannot reference an identifier before its definition
  in module: top-level
  context...:
   eval-one-top12
   /usr/share/racket/pkgs/sandbox-lib/racket/sandbox.rkt:510:0: call-with-custodian-shutdown
   /usr/share/racket/collects/racket/private/more-scheme.rkt:148:2: call-with-break-parameterization
   .../more-scheme.rkt:261:28
   /usr/share/racket/pkgs/sandbox-lib/racket/sandbox.rkt:878:5: loop


### Problem 2 (10 points)

Write the following two procedures.  Remember to use the instruction
selectors: ins-c-state, ins-c-symbol, ins-n-state, ins-n-symbol,
ins-dir
<pre>
(i-match? state symbol inst)
</pre>

returns <code>#t</code> if state and symbol are equal to the state and symbol of
instruction inst otherwise returns <code>#f</code>
<pre>
(i-lookup state symbol mach)
</pre>

returns <code>#f</code> if no instruction of Turing machine mach has state and
symbol equal to state and symbol otherwise returns the instruction
in mach that matches.  You may assume that at most one instruction
will match.

The latter point is based on the requirement that Turing machines be
deterministic, that is, there is only one way to execute a given
program for a given input.  The alternative is non-determinism,
as mentioned in class.

For this assignment, when writing Turing machine programs (problems
1, 7, and 8) be certain that no two instructions have the same
<code>c-symbol</code> and <code>c-state</code> (with possibly differing <code>n-state</code>, <code>n-symbol</code>, or <code>dir</code>).

Examples

<pre>
(i-match? 'q1 'b (ins 'q1 'b 'q3 'b 'L)) => #t
(i-match? 'q1  0  (ins 'q1 1 'q4 1 'L)) => #f
(i-match? 'q2 1 (ins 'q2 1 'q2 1 'L)) => #t
(equal? (i-lookup 'q1 1 tm1) (ins 'q1 1 'q1 0 'R)) => #t
(equal? (i-lookup 'q2 'b tm1) (ins 'q2 'b 'q3 'b 'R)) => #t
(i-lookup 'q3 1 tm1) => #f
</pre>

In [21]:
(define (i-match? state symbol inst)
  empty)

In [22]:
(define (i-lookup state symbol mach)
  empty)

### Representation of a Turing machine configuration.

We represent a Turing machine configuration using the following structure:

In [23]:
(struct conf (state ltape symbol rtape) #:transparent)

where 
- <code>state</code> is the current state of the machine,
- <code>ltape</code> is a list of symbols to the left of the currently scanned symbol,
- <code>symbol</code> is the currently scanned symbol,
- <code>rtape</code> is a list of symbols to the right of the currently scanned symbol.

We reserve the symbol <code>'b</code> for the blank.

For example, we define the following two configurations:

In [24]:
(define config1 (conf 'q3 '(0 0) 1 '(1)))
(define config2 (conf 'q6 '(1 b) 0 '(b b)))

In [25]:
config1

(conf 'q3 '(0 0) 1 '(1))

In [26]:
config2

(conf 'q6 '(1 b) 0 '(b b))

Note that the selectors are
<code>conf-state, conf-ltape, conf-symbol, conf-rtape</code>

<code>config1</code> represents the Turing machine configuration


<pre>

   --------------------------
   .. | 0 | 0 | 1 | 1 |  | ..
   --------------------------
                ^
                q3

</pre>

in which the non-blank symbols on the tape are 0011,
and the machine is in state <code>q3</code> with the read/write head
scanning the leftmost 1.

<code>config2</code> represents the Turing machine configuration


<pre>

   ------------------------------
   .. |   | 1 |  | 0 |   |   | ..
   ------------------------------
                   ^
                   q6

</pre>



in which the symbols 1, blank, 0, are on the tape, surrounded
by blanks, and the machine is in state <code>q6</code> with the read/write
head scanning the 0.

A configuration is *normalized* if neither the first symbol of
<code>ltape</code> nor the last symbol of <code>rtape</code> is the symbol <code>'b</code>.
Of the two configurations above, <code>config1</code> is normalized, 
but <code>config2</code> is not (the last element of its <code>rtape</code> list is <code>'b</code>.)

Note that tape squares not explicitly represented are
assumed to contain blanks.  A normalized configuration
to represent the machine in state q1 with all tape squares
blank is thus <code>(conf 'q1 '() 'b '()))</code>.

### Problem 3 (9 points)

Write the following three procedures.

<code>(halted? mach config)</code>
returns <code>#t</code> if the Turing machine mach is halted in machine configuration config 
(ie, no instruction of the machine matches the current state and symbol 
in configuration config) and returns <code>#f</code> otherwise.

<code>(change-state new-state config)</code>
takes a configuration <code>config</code> and returns a configuration
in which the state of the machine is changed to <code>new-state</code>.

<code>(write-symbol new-symbol config)</code> takes a configuration <code>config</code> and
returns a configuration in which the symbol scanned by 
the read/write head has been replaced by <code>new-symbol</code>.


Examples
<pre>
(halted? tm1 (conf 'q1 '(1 1 0) 'b '())) => #f
(halted? (list (ins 'q1 'b 'q2 'b 'R)) (conf 'q2 '() 'b '())) => #t
(change-state 'q2 (conf 'q1 '(0) 1 '())) => (conf 'q2 '(0) 1 '())
(change-state 'q13 (conf 'q4 '(0 1 1) 'b '())) => (conf 'q13 '(0 1 1) 'b '())
(write-symbol 1 (conf 'q5 '(0) 0 '(1 1))) => (conf 'q5 '(0) 1 '(1 1))
(write-symbol 'c (conf 'q2 '(0 0 1) 1 '(1 1))) => (conf 'q2 '(0 0 1) 'c '(1 1))
(write-symbol 'b (conf 'q3 '(1) 0 '())) => (conf 'q3 '(1) 'b '())
</pre>

In [27]:
(define (halted? mach config)
  empty)

In [28]:
(define (change-state new-state config)
  empty)

In [29]:
(define (write-symbol new-symbol config)
  empty)

### Problem 4 ** (10 points)

Write one procedure

<code>(normalize config)</code>
takes a Turing machine configuration <code>config</code> and returns an equivalent 
*normalized*  configuration. That is, the same Turing machine configuration is
represented by the input configuration and the output configuration, 
and the output configuration does not have a <code>'b</code> as the first element 
of its ltape list or the last element of its rtape list.

Examples
<pre>
(normalize config1) => (conf 'q3 '(0 0) 1 '(1))
(normalize config2) => (conf 'q6 '(1 b) 0 '())
(normalize (conf 'q3 '(b 0) 'b '(1 1 0 b b))) => (conf 'q3 '(0) 'b '(1 1 0))
(normalize (conf 'q6 '(b 0 b 0) 1 '(0 b 0 b))) => (conf 'q6 '(0 b 0) 1 '(0 b 0))
(normalize (conf 'q4 '(b b) 'b '(b b b))) => (conf 'q4 '() 'b '())
</pre>

In [30]:
(define (normalize config)
  empty)

### Problem 5 ** (10 points)

Write two procedures

<code>(shift-head-left config)</code>
takes a normalized configuration config and returns a normalized configuration 
in which the position of the read/write head has been moved one tape square 
to the left.

<code>(shift-head-right config)</code>
takes a normalized configuration config and returns a normalized configuration 
in which the position of the read/write head has been moved one tape square 
to the right.

Examples
<pre>
(shift-head-left (conf 'q5 '() 'b '())) => (conf 'q5 '() 'b '())
(shift-head-left (conf 'q6 '(0 0) 1 '(1 1))) => (conf 'q6 '(0) 0 '(1 1 1))
(shift-head-left (conf 'q7 '() 0 '(1 1 0))) => (conf 'q7 '() 'b '(0 1 1 0))
(shift-head-right (conf 'q2 '() 'b '())) => (conf 'q2 '() 'b '())
(shift-head-right (conf 'q9 '() 0 '(1 1 1))) => (conf 'q9 '(0) 1 '(1 1))
(shift-head-right (conf 'q8 '(1 0 1 1) 'b '())) => (conf 'q8 '(1 0 1 1 b) 'b '())
</pre>

Hint:

last element of a list is built in to Racket <code>(last lst)</code>

all but last element of a list -- uses Racket's <code>drop-right</code>

In [31]:
(define (shift-head-left config)
  empty)

In [32]:
(define (shift-head-right config)
  empty)

### Problem 6 ** (15 points)

Write a procedure 

<code>(next-config mach config)</code>
takes a Turing machine <code>mach</code> and a normalized configuration <code>config</code>
and returns the normalized next configuration 
for the Turing machine <code>mach</code> in the configuration <code>config</code>.
If there is no applicable instruction, the configuration
returned should be just the input configuration.

Hint: get your procedures
<code>halted?, i-lookup, change-state, write-symbol, shift-head-left, shift-head-right</code>
working and combine them appropriately.

Examples
<pre>
(next-config tm1 (conf 'q1 '() 0 '(0 1))) => (conf 'q1 '(1) 0 '(1))
(next-config tm1 (conf 'q1 '(1) 0 '(1))) => (conf 'q1 '(1 1) 1 '())
(next-config tm1 (conf 'q1 '(1 1 0) 'b '())) => (conf 'q2 '(1 1) 0 '())
(next-config tm1 (conf 'q2 '() 'b '(1 1 0))) => (conf 'q3 '() 1 '(1 0))
(next-config tm1 (conf 'q3 '() 1 '(1 0))) => (conf 'q3 '() 1 '(1 0))
</pre>

In [33]:
(define (next-config mach config)
  empty)

If your procedures are working, then you should
be able to run the following example, which
shows the successive normalized configurations 
of Turing machine tm1 when run from the given configuration.

<pre>
> (simulate tm1 (conf 'q1 '() 1 '(1 0 1 0)) 20)
(list
 (conf 'q1 '() 1 '(1 0 1 0))
 (conf 'q1 '(0) 1 '(0 1 0))
 (conf 'q1 '(0 0) 0 '(1 0))
 (conf 'q1 '(0 0 1) 1 '(0))
 (conf 'q1 '(0 0 1 0) 0 '())
 (conf 'q1 '(0 0 1 0 1) 'b '())
 (conf 'q2 '(0 0 1 0) 1 '())
 (conf 'q2 '(0 0 1) 0 '(1))
 (conf 'q2 '(0 0) 1 '(0 1))
 (conf 'q2 '(0) 0 '(1 0 1))
 (conf 'q2 '() 0 '(0 1 0 1))
 (conf 'q2 '() 'b '(0 0 1 0 1))
 (conf 'q3 '() 0 '(0 1 0 1)))
</pre>

### Problem 7 ** (15 points)

Define (in the given representation) a Turing machine named

<code>tm-convert</code>

that takes as input a positive integer <code>n</code> represented in binary
and produces as output a string of <code>n x</code>'s.  When the machine
halts, the read/write head should be positioned over the
leftmost <code>x</code> in the output string.  The start state should be named
<code>q1</code> -- other states may be named by any other Racket symbols.

You *may* use additional tape symbols.  When the machine halts,
there should be just <code>n x</code>'s, surrounded by blanks, on the tape.

<b>IMPORTANT:</b> Give a clear overview description of how your Turing machine works.

<b>NOTE:</b> you can still do this problem if your simulator is not working, 
assuming you understand Turing machines and the representation of them 
defined above.

Examples of the behavior of tm-convert
<pre>
1            => x
11           => xxx
110          => xxxxxx
1111         => xxxxxxxxxxxxxxx

(test 'tm-convert (simulate-lite tm-convert (conf 'q1 '() 1 '()) 20) '(() x ()))
(test 'tm-convert (simulate-lite tm-convert (conf 'q1 '() 1 '(1)) 200) '(() x (x x)))
(test 'tm-convert (simulate-lite tm-convert (conf 'q1 '() 1 '(1 0)) 200) '(() x (x x x x x)))
(test 'tm-convert (simulate-lite tm-convert (conf 'q1 '() 1 '(1 1 1)) 400) '(() x (x x x x x x x x x x x x x x)))
</pre>

Here are input configurations if you want to simulate your tm-convert on
these inputs.

In [36]:
(define conv1 (conf 'q1 '() 1 '()))
(define conv6 (conf 'q1 '() 1 '(1 0)))
(define conv15 (conf 'q1 '() 1 '(1 1 1)))
(define conv64 (conf 'q1 '() 1 '(0 0 0 0 0 0)))

In [37]:
conv1

(conf 'q1 '() 1 '())

In [38]:
conv6

(conf 'q1 '() 1 '(1 0))

In [39]:
conv15

(conf 'q1 '() 1 '(1 1 1))

In [40]:
conv64

(conf 'q1 '() 1 '(0 0 0 0 0 0))

In [41]:
(define tm-convert
  empty)

Examples of the behavior of <code>tm-sort</code>
<pre>
0          => 0  
1          => 1
00         => 00
110        => 011
1011011    => 0011111

(test 'tm-sort (simulate-lite tm-sort (conf 'q1 '() 0 '()) 20) '(() 0 ()))
(test 'tm-sort (simulate-lite tm-sort (conf 'q1 '() 1 '()) 20) '(() 1 ()))
(test 'tm-sort (simulate-lite tm-sort (conf 'q1 '() 0 '(0)) 200) '(() 0 (0)))
(test 'tm-sort (simulate-lite tm-sort (conf 'q1 '() 1 '(1 0)) 200) '(() 0 (1 1)))
(test 'tm-sort (simulate-lite tm-sort (conf 'q1 '() 1 '(0 1 1 0 1 1)) 200) '(() 0 (0 1 1 1 1 1)))
</pre>

Here are some input configurations if you want to simulate your tm-sort on
these inputs.

In [42]:
(define sort0 (conf 'q1 '() 0 '()))
(define sort1 (conf 'q1 '() 1 '()))
(define sort00 (conf 'q1 '() 0 '(0)))
(define sort110 (conf 'q1 '() 1 '(1 0)))
(define sort-long (conf 'q1 '() 1 '(0 1 1 0 1 1)))

In [43]:
sort0

(conf 'q1 '() 0 '())

In [44]:
sort1

(conf 'q1 '() 1 '())

In [45]:
sort00

(conf 'q1 '() 0 '(0))

In [46]:
sort110

(conf 'q1 '() 1 '(1 0))

In [47]:
sort-long

(conf 'q1 '() 1 '(0 1 1 0 1 1))

In [48]:
(define tm-sort
  empty)